In [326]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import pandas as pd
from matplotlib.gridspec import GridSpec
from tqdm.auto import tqdm

plt.rcParams['text.usetex'] = True
plt.rcParams['text.latex.preamble'] = r'\usepackage{amsmath}'


font = {'family': 'serif',
        'weight': 'normal',
        'size': 14,
        }

font1 = {'family': 'serif',
        'weight': 'normal',
        'size': 16,
        }

font2 = {'family': 'serif',
        'weight': 'normal',
        'size': 10,
        }

# Load solutions

In [327]:
r0 = 5
rs = 1/2
delta = 1e-5
PsiAgrb = 0.55

dfi_sup = pd.read_csv("grb_sup.txt", sep = "\t", header = 0)
dfi_sub = pd.read_csv("grb_sub.txt", sep = "\t", header = 0)
dfr1_sup = pd.read_csv("grb_tanh_29.5_6_25.txt", sep = "\t", header = 0)
dfr2_sup = pd.read_csv("grb_tanh_970_50_25.txt", sep = "\t", header = 0)

len_sup = dfi_sup.shape[0]
len_sub = dfi_sub.shape[0]

r1 = np.linspace(r0 + delta, 50000, len_sup)
r2 = np.linspace(r0 - delta, 3.5, len_sub)

In [328]:
A0_sup = np.array([dfi_sup['Flux Function'].to_numpy(), 
          dfr1_sup['Flux Function'].to_numpy(), 
          dfr2_sup['Flux Function'].to_numpy()])

Bφ0_sup = np.array([dfi_sup['Azimuthal Magnetic Field'].to_numpy(), 
           dfr1_sup['Azimuthal Magnetic Field'].to_numpy(), 
           dfr2_sup['Azimuthal Magnetic Field'].to_numpy()])

F_sup = np.array([dfi_sup['Expansion Factor'].to_numpy(), 
         dfr1_sup['Expansion Factor'].to_numpy(), 
         dfr2_sup['Expansion Factor'].to_numpy()])

A0_sub = np.array([dfi_sub['Flux Function'].to_numpy(), dfi_sub['Flux Function'].to_numpy(), dfi_sub['Flux Function'].to_numpy()])

Bφ0_sub = np.array([dfi_sub['Azimuthal Magnetic Field'].to_numpy(), dfi_sub['Azimuthal Magnetic Field'].to_numpy(), dfi_sub['Azimuthal Magnetic Field'].to_numpy()])

F_sub = np.array([dfi_sub['Expansion Factor'].to_numpy(), dfi_sub['Expansion Factor'].to_numpy(), dfi_sub['Expansion Factor'].to_numpy()])

In [329]:
h0 = lambda r: np.sqrt(1 - rs/r) # Lapse function

R = lambda r, theta: (r/rs)*theta # Cylindrical radius

Z = lambda r, theta: (r/rs)*(1 - 0.5*theta**2) # Height above midplane

theta_A = lambda r, theta, A0: np.sqrt(A0[0]/A0)*theta # Magnetic field line shape 

# Construct field lines from solutions

In [330]:
theta_b = 0.2

theta_in = np.linspace(0, theta_b, 101)

theta_flux_sup = np.zeros((len(A0_sup), len(theta_in), len(r1)))
x_sup = np.zeros((len(A0_sup), len(theta_in), len(r1)))
z_sup = np.zeros((len(A0_sup), len(theta_in), len(r1)))

theta_flux_sub = np.zeros((len(A0_sup), len(theta_in), len(ragn)))
x_sub = np.zeros((len(A0_sup), len(theta_in), len(ragn)))
z_sub = np.zeros((len(A0_sup), len(theta_in), len(ragn)))

for i in tqdm(range(len(A0_sup)), desc = 'Loading Jet Models'):
    for j in range(len(theta_in)):
        theta_flux_sup[i,j,:] = theta_A(r1, theta_in[j], A0_sup[i])
        x_sup[i,j,:] = R(r1, theta_flux_sup[i,j,:])
        z_sup[i,j,:] = Z(r1, theta_flux_sup[i,j,:])
         
        theta_flux_sub[i,j,:] = theta_A(r2, theta_in[j], A0_sub[i])
        x_sub[i,j,:] = R(r2, theta_flux_sub[i,j,:])
        z_sub[i,j,:] = Z(r2, theta_flux_sub[i,j,:])

Loading Jet Models:   0%|          | 0/3 [00:00<?, ?it/s]

In [332]:
x = np.concatenate((x_sub[:,:,::-1], x_sup), axis = 2)

z = np.concatenate((z_sub[:,:,::-1], z_sup), axis = 2)

A0 = np.concatenate((A0_sub[:,::-1], A0_sup), axis = 1)

F = np.concatenate((F_sub[:,::-1], F_sup), axis = 1)

Bφ0 = np.concatenate((Bφ0_sub[:,::-1], Bφ0_sup), axis = 1)

theta_flux = np.concatenate((theta_flux_sub[:,:,::-1], theta_flux_sup), axis = 2)

rp = np.concatenate((r2[::-1], r1))/rs



Bp = np.sqrt((2*A0/rp**2 - theta_flux[:,-1,:]**2*A0/rp**2)**2 + (theta_flux[:,-1,:]*F*A0/rp)**2)

φB = np.arctan((Bp/(Bφ0*theta_flux[:,-1,:])))

# Construct black hole

In [333]:
phi_bh = np.linspace(0, 2*np.pi, 100)
theta_bh = np.linspace(0, np.pi, 100)
x_bh = np.outer(np.cos(phi_bh), np.sin(theta_bh))
y_bh = np.outer(np.sin(phi_bh), np.sin(theta_bh))
z_bh = np.outer(np.ones(np.size(phi_bh)), np.cos(theta_bh))

# Construct plot

In [334]:
save_dir = ''

In [335]:
s = 10500
s1 = -1

fig = plt.figure(dpi=600, figsize=(23, 31))

left, bottom, width, height = 0.1, 0.6, 0.3, 0.5
gap = 0.0

ax1 = fig.add_axes([left, bottom, width, height], projection='3d')
ax2 = fig.add_axes([left + width + gap, bottom, width, height], projection='3d')
ax3 = fig.add_axes([left + 2*(width + gap), bottom, width, height], projection='3d')
ax4 = fig.add_axes([left + 0.08, 0.54, 0.78, 0.2])

axes = [ax1, ax2, ax3]
colors = ['k', 'mediumseagreen', 'purple']
titles = [r'Ideal', r'Res1', r'Res2']

for i, ax in enumerate(axes):
    
    [ax.plot(x[i, -1,:s]*np.sin(-φB[i, :s]**(-1) + j*np.pi/3), 
             x[i, -1,:s]*np.cos(-φB[i, :s]**(-1) + j*np.pi/3), 
             z[i, -1,:s], lw=1.0, c = colors[i]) for j in range(6)]
    
    ax.plot_surface(x_bh, y_bh, z_bh, color = 'k', alpha=1)
    
    ax.xaxis._axinfo["grid"].update({"linewidth": 0.25})
    ax.yaxis._axinfo["grid"].update({"linewidth": 0.25})
    ax.zaxis._axinfo["grid"].update({"linewidth": 0.25})
    ax.set_xlabel(r'$x\, [r_{S}]$', labelpad=10, fontsize=20)
    ax.set_ylabel(r'$y\, [r_{S}]$', labelpad=15, fontsize=20)
    ax.set_zlabel(r'$z\, [r_{S}]$', labelpad=45, fontsize=20)
    ax.xaxis.set_tick_params(pad=0)
    ax.yaxis.set_tick_params(pad=0)
    ax.zaxis.set_tick_params(pad=15)
    ax.set_aspect('equal')
    ax.xaxis.set_ticks([-30, 0, 30])
    ax.yaxis.set_ticks([-30, 0, 30])
    ax.zaxis.set_ticks([0, 50, 100, 150, 200, 250])
    ax.xaxis.set_ticklabels([r'$-30$', r'$0$', r'$30$'], fontsize=18)
    ax.yaxis.set_ticklabels([r'$-30$', r'$0$', r'$30$'], fontsize=18)
    ax.zaxis.set_ticklabels([r'$0$', r'$50$', r'$100$', r'$150$', r'$200$', r'$250$'], fontsize=18)
    ax.xaxis.set_pane_color((1.0, 1.0, 1.0, 0.0))
    ax.yaxis.set_pane_color((1.0, 1.0, 1.0, 0.0))
    ax.zaxis.set_pane_color((1.0, 1.0, 1.0, 0.0))
    ax.set_xlim(-60, 60)
    ax.set_ylim(-60, 60)
    ax.set_title(titles[i], fontsize=24)

[ax4.loglog(z[i,-1,:], -Bpagn[i,-1]/(Bφ0[i]*θflux[i,-1]), c = colors[i], label = titles[i]) for i in range(3)];

ax4.set_xlabel(r'$z\, [r_{S}]$', fontsize = 28)
ax4.set_ylabel(r'$\frac{|B_{p}|}{|B_{\phi}|}$', rotation = 0, fontsize = 36, labelpad = 36)
ax4.legend(fontsize = 20, fancybox = True, shadow = True)
ax4.set_aspect(0.2)
ax4.xaxis.set_ticks([1e0, 1e1, 1e2, 1e3, 1e4, 1e5])
ax4.yaxis.set_ticks([1e-3,1e-2, 1e-1, 1e0, 1e1])
ax4.xaxis.set_ticklabels([r'$10^{0}$', r'$10^{1}$', r'$10^{2}$', r'$10^{3}$', r'$10^{4}$', r'$10^{5}$'], fontsize=20)
ax4.yaxis.set_ticklabels([r'$10^{-3}$', r'$10^{-2}$', r'$10^{-1}$', r'$10^{0}$', r'$10^{1}$'], fontsize=20)
ax4.xaxis.set_tick_params(direction = 'in', which = 'both', pad = 10)
ax4.yaxis.set_tick_params(direction = 'in', which = 'both', pad = 5)
ax4.text(1e3, 0.8, r'$\sim z^{-1}$', fontsize = 30, color = 'crimson')
ax4.axvline(1e1, ymax = 0.175, c = 'k', ls = '--')
ax4.axvline(1e1, ymin = 0.542, c = 'k', ls = '--')
ax4.text(9.2, 5.0e-4, r'Alfvén Surface', fontsize = 20, rotation = 90, color = 'k')
ax4.set_xlim(4e0, 1.5e5);

# fig.savefig(f'{save_dir}/jet_field_lines.pdf', format = 'pdf', bbox_inches='tight')